In [1]:
import pandas as pd
import numpy as np

In [281]:
ratings=pd.read_csv("archive (5)/rating.csv",parse_dates=["timestamp"])

In [282]:
ratings

userId  movieId  rating           timestamp
0              1        2     3.5 2005-04-02 23:53:47
1              1       29     3.5 2005-04-02 23:31:16
2              1       32     3.5 2005-04-02 23:33:39
3              1       47     3.5 2005-04-02 23:32:07
4              1       50     3.5 2005-04-02 23:29:40
...          ...      ...     ...                 ...
20000258  138493    68954     4.5 2009-11-13 15:42:00
20000259  138493    69526     4.5 2009-12-03 18:31:48
20000260  138493    69644     3.0 2009-12-07 18:10:57
20000261  138493    70286     5.0 2009-11-13 15:42:24
20000262  138493    71619     2.5 2009-10-17 20:25:36

[20000263 rows x 4 columns]

In [283]:
rand_userIds = np.random.choice(ratings['userId'].unique(), 
                                size=int(len(ratings['userId'].unique())*0.3), 
                                replace=False)
ratings = ratings.loc[ratings['userId'].isin(rand_userIds)]

In [284]:
len(rand_userIds)

41547

In [285]:
ratings["rank_latest"]=ratings.groupby(["userId"])["timestamp"].rank(method="first",ascending=False)
num_movies=len(ratings["movieId"].unique())
test_ratings=ratings[ratings["rank_latest"]==1]
ratings=ratings[ratings["rank_latest"]!=1]
test_ratings=test_ratings[["userId","movieId","rating"]]
ratings=ratings[["userId","movieId","rating"]]

<ipython-input-285-324a8e4c5a2e>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ratings["rank_latest"]=ratings.groupby(["userId"])["timestamp"].rank(method="first",ascending=False)


In [286]:
ratings.loc[:,"rating"]=1

In [287]:
ratings

userId  movieId  rating
451            5        2       1
452            5       11       1
453            5       17       1
454            5       60       1
455            5       62       1
...          ...      ...     ...
19999630  138489     2959       1
19999631  138489     3671       1
19999632  138489     4973       1
19999633  138489     5291       1
19999634  138489    58559       1

[5919425 rows x 3 columns]

In [290]:
test_ratings["userId"].count()

41547

In [291]:
len(ratings["movieId"].unique())

20817

In [292]:
len(test_ratings["movieId"].unique())

6212

In [293]:
#num_users=len(training["userId"].unique())
#num_users=ratings["userId"].max()+1
num_users=ratings["userId"].max()+1
num_movies=ratings["movieId"].max()+1

In [294]:
num_users

138490

In [295]:
all_movie_ids=ratings["movieId"].unique()

user,movies,labels=[],[],[]
user_item_set=set(zip(ratings["userId"],ratings["movieId"]))

num_negatives=4

for (u,i) in user_item_set:
    
    user.append([u])
    movies.append([i])
    labels.append(1)
    for _ in range(num_negatives):
        negative_item=np.random.choice(all_movie_ids)
        while(u,negative_item) in user_item_set:
            negative_item=np.random.choice(all_movie_ids)
        user.append([u])
        movies.append([negative_item])
        labels.append(0)

In [296]:
test=[]
for i in test_ratings["movieId"]:
    count=0
    for j in all_movie_ids:
        if i==j:
            count=1
            break
    if count==0:
        test.append(i)
len(test)
    

28

In [299]:
users_movies_labels=list(zip(user,movies,labels))

In [300]:
import random
random.shuffle(users_movies_labels)

In [301]:
users,movies,labels=zip(*users_movies_labels)

In [302]:
user=list(users)
movies=list(movies)
labels=list(labels)

In [303]:
from keras import utils
from keras.preprocessing.text import Tokenizer

In [304]:
labels=np.array(labels)

In [305]:
x_train_user=utils.pad_sequences(user,maxlen=1)
x_train_movies=utils.pad_sequences(movies,maxlen=1)

In [306]:
labels=np.asarray(labels.astype("int32").reshape(-1,1))

In [307]:
x_train_movies.shape

(29597125, 1)

In [308]:
x_train_user.shape

(29597125, 1)

In [309]:
len(labels)

29597125

In [310]:
labels.shape

(29597125, 1)

In [311]:
num_movies

131171

In [312]:
x_train_user.shape

(29597125, 1)

In [55]:
#functional api implementation using two inputs

In [313]:
from keras.models import Model
from keras import layers
from keras import Input
from keras import Sequential

In [314]:
user_input=Input(shape=(None,),dtype="int32",name="user")
embedded_user=layers.Embedding(num_users,8)(user_input)

movie_input=Input(shape=(None,),dtype="int32",name="movie")
embedded_movies=layers.Embedding(num_movies,8)(movie_input)


concatenated=layers.concatenate([embedded_user,embedded_movies],axis=-1)
answer=layers.Dense(64,activation="relu")(concatenated)
answer=layers.Dense(32,activation="relu")(answer)

answer=layers.Dense(1,activation="sigmoid")(answer)
model=Model([user_input,movie_input],answer)

In [315]:
model.compile(optimizer="rmsprop",loss="binary_crossentropy",metrics=["acc"])


In [316]:
model.summary()

Model: "model_13"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 user (InputLayer)              [(None, None)]       0           []                               
                                                                                                  
 movie (InputLayer)             [(None, None)]       0           []                               
                                                                                                  
 embedding_26 (Embedding)       (None, None, 8)      1107920     ['user[0][0]']                   
                                                                                                  
 embedding_27 (Embedding)       (None, None, 8)      1049368     ['movie[0][0]']                  
                                                                                           

In [319]:
model.fit([x_train_user,x_train_movies],labels,epochs=1,validation_split=0.3)

647438/647438 [==============================] - 7365s 11ms/step - loss: 0.2397 - acc: 0.9024 - val_loss: 0.2483 - val_acc: 0.9026


In [322]:
recommender_model=model.save("recommender_model")

INFO:tensorflow:Assets written to: recommender_model/assets


INFO:tensorflow:Assets written to: recommender_model/assets


array([16501], dtype=int32)

In [323]:
model.predict([x_train_user[252],x_train_movies[252]])

1/1 [==============================] - 0s 83ms/step


array([[0.7424059]], dtype=float32)

In [324]:
test_ratings

userId  movieId  rating
511            5     1136     5.0
524            6      140     4.0
1231          11     5971     5.0
1792          14    46062     3.5
1837          15      497     3.0
...          ...      ...     ...
19999112  138483      608     4.0
19999314  138485    48516     5.0
19999482  138486     8957     5.0
19999578  138488      207     3.0
19999628  138489     2858     4.0

[41547 rows x 3 columns]

In [325]:
test_user_item_set = set(zip(test_ratings['userId'], test_ratings['movieId']))

In [326]:
user_interacted_items = ratings.groupby('userId')['movieId'].apply(list).to_dict()

In [335]:
results=0
for (u,i) in test_user_item_set:
    max_10_movies=[0,0,0,0,0,0,0,0,0,0]
    max_10=[0,0,0,0,0,0,0,0,0,0]
    count=0
    interacted_items=user_interacted_items[u]
    not_interacted_items=set(all_movie_ids)-set(interacted_items)
    selected_not_interacted=list(np.random.choice(list(not_interacted_items),99))
    
    user=[]
    movies=[]
    labels=[]
    for k in range(100):
        user.append([u])
        if(k==0):
            movies.append([i])
            labels.append([1])
        else:
            movies.append([selected_not_interacted[k-1]])
            labels.append([0])
    users_movies_labels=list(zip(user,movies,labels))
    random.shuffle(users_movies_labels)
    users,movies,labels=zip(*users_movies_labels)
    user=list(users)
    movies=list(movies)
    labels=list(labels)
    labels=np.array(labels)
    x_test_user=utils.pad_sequences(user,maxlen=1)
    x_test_movies=utils.pad_sequences(movies,maxlen=1)
    labels=np.asarray(labels.astype("int32").reshape(-1,1))
    
    for j in range(len(labels)):
        if (x_test_movies[j][0]==i):
            print("the real one")
            print(i)
            count=1
        
#        predictions=model.predict([x_test_user[j],x_test_movies[j]])
#        for k in range(10):
#            if predictions>max_10[k]:
#                max_10[k]=predictions
#                max_10_movies[k]=x_train_movies[j][0]
                    
            
        
        if count==1:
            
            predictions=model.predict([x_test_user[j],x_test_movies[j]])
            if predictions>=0.5:
                results+=1
            print("For user:{},  ".format(u))
            print("the real recommendation:",x_test_movies[j])
            print(predictions)
            break
            
            #predictions=model.predict([x_test_user[j],x_test_movies[j]])
            #print("For user:{},  ".format(u))
            #print("the real recommendation:",x_test_movies[j])
            #print(predictions)
#    for k in range(10):
#       if max_10_movies[k]==i:
#            print("WE GOT IT")
    print("Results:{}".format(results))
            
    
    

the real one
1500
1/1 [==============================] - 0s 22ms/step
For user:122444,  
the real recommendation: [1500]
[[0.8510949]]
Results:1
the real one
8
1/1 [==============================] - 0s 21ms/step
For user:15673,  
the real recommendation: [8]
[[0.2554572]]
Results:1
the real one
3167
1/1 [==============================] - 0s 20ms/step
For user:18632,  
the real recommendation: [3167]
[[0.22732262]]
Results:1
the real one
1517
1/1 [==============================] - 0s 20ms/step
For user:25318,  
the real recommendation: [1517]
[[0.9781043]]
Results:2
the real one
44195
1/1 [==============================] - 0s 21ms/step
For user:20727,  
the real recommendation: [44195]
[[0.7424059]]
Results:3
the real one
940
1/1 [==============================] - 0s 21ms/step
For user:10847,  
the real recommendation: [940]
[[0.47542673]]
Results:3
the real one
1682
1/1 [==============================] - 0s 21ms/step
For user:81626,  
the real recommendation: [1682]
[[0.992534]]
Result

1/1 [==============================] - 0s 20ms/step
For user:112343,  
the real recommendation: [4396]
[[0.33755264]]
Results:36
the real one
1061
1/1 [==============================] - 0s 20ms/step
For user:135913,  
the real recommendation: [1061]
[[0.69738215]]
Results:37
the real one
1620
1/1 [==============================] - 0s 19ms/step
For user:67983,  
the real recommendation: [1620]
[[0.549638]]
Results:38
the real one
1483
1/1 [==============================] - 0s 20ms/step
For user:27499,  
the real recommendation: [1483]
[[0.4171564]]
Results:38
the real one
260
1/1 [==============================] - 0s 20ms/step
For user:59421,  
the real recommendation: [260]
[[0.99845344]]
Results:39
the real one
55820
1/1 [==============================] - 0s 20ms/step
For user:127319,  
the real recommendation: [55820]
[[0.7424059]]
Results:40
the real one
1
1/1 [==============================] - 0s 20ms/step
For user:131043,  
the real recommendation: [1]
[[0.9980144]]
Results:41
the

1/1 [==============================] - 0s 20ms/step
For user:37927,  
the real recommendation: [354]
[[0.22883977]]
Results:73
the real one
8874
1/1 [==============================] - 0s 20ms/step
For user:2856,  
the real recommendation: [8874]
[[0.9988022]]
Results:74
the real one
481
1/1 [==============================] - 0s 20ms/step
For user:67466,  
the real recommendation: [481]
[[0.5702712]]
Results:75
the real one
1033
1/1 [==============================] - 0s 20ms/step
For user:73737,  
the real recommendation: [1033]
[[0.5003892]]
Results:76
the real one
160
1/1 [==============================] - 0s 20ms/step
For user:71996,  
the real recommendation: [160]
[[0.8297827]]
Results:77
the real one
5971
1/1 [==============================] - 0s 20ms/step
For user:40385,  
the real recommendation: [5971]
[[0.5670827]]
Results:78
the real one
2959
1/1 [==============================] - 0s 20ms/step
For user:65113,  
the real recommendation: [2959]
[[0.99750215]]
Results:79
the rea

1/1 [==============================] - 0s 22ms/step
For user:44813,  
the real recommendation: [3972]
[[0.46502435]]
Results:116
the real one
62374
1/1 [==============================] - 0s 21ms/step
For user:55237,  
the real recommendation: [62374]
[[0.25275016]]
Results:116
the real one
32
1/1 [==============================] - 0s 22ms/step
For user:92946,  
the real recommendation: [32]
[[0.9983941]]
Results:117
the real one
64839
1/1 [==============================] - 0s 22ms/step
For user:124146,  
the real recommendation: [64839]
[[0.60522234]]
Results:118
the real one
6539
1/1 [==============================] - 0s 21ms/step
For user:34023,  
the real recommendation: [6539]
[[0.99907005]]
Results:119
the real one
47
1/1 [==============================] - 0s 21ms/step
For user:101426,  
the real recommendation: [47]
[[0.99754983]]
Results:120
the real one
3564
1/1 [==============================] - 0s 21ms/step
For user:103889,  
the real recommendation: [3564]
[[0.37639466]]
Res

1/1 [==============================] - 0s 20ms/step
For user:41636,  
the real recommendation: [7587]
[[0.1967778]]
Results:190
the real one
62
1/1 [==============================] - 0s 20ms/step
For user:108587,  
the real recommendation: [62]
[[0.8608748]]
Results:191
the real one
2070
1/1 [==============================] - 0s 20ms/step
For user:86859,  
the real recommendation: [2070]
[[0.3640505]]
Results:191
the real one
58559
1/1 [==============================] - 0s 20ms/step
For user:91215,  
the real recommendation: [58559]
[[0.87083066]]
Results:192
the real one
8641
1/1 [==============================] - 0s 20ms/step
For user:101399,  
the real recommendation: [8641]
[[0.61456525]]
Results:193
the real one
7158
1/1 [==============================] - 0s 20ms/step
For user:112146,  
the real recommendation: [7158]
[[0.38323542]]
Results:193
the real one
7361
1/1 [==============================] - 0s 20ms/step
For user:64422,  
the real recommendation: [7361]
[[0.9992926]]
Resu

...

1/1 [==============================] - 0s 20ms/step
For user:70060,  
the real recommendation: [1580]
[[0.9965248]]
Results:27136
the real one
5648
1/1 [==============================] - 0s 21ms/step
For user:10141,  
the real recommendation: [5648]
[[0.02617837]]
Results:27136
the real one
4016
1/1 [==============================] - 0s 21ms/step
For user:65065,  
the real recommendation: [4016]
[[0.575253]]
Results:27137
the real one
639
1/1 [==============================] - 0s 20ms/step
For user:122575,  
the real recommendation: [639]
[[0.2391046]]
Results:27137
the real one
8783
1/1 [==============================] - 0s 21ms/step
For user:95016,  
the real recommendation: [8783]
[[0.5677511]]
Results:27138
the real one
1042
1/1 [==============================] - 0s 20ms/step
For user:39540,  
the real recommendation: [1042]
[[0.7167716]]
Results:27139
the real one
2600
1/1 [==============================] - 0s 20ms/step
For user:33825,  
the real recommendation: [2600]
[[0.5955571

1/1 [==============================] - 0s 20ms/step
For user:6773,  
the real recommendation: [1367]
[[0.7424059]]
Results:27216
the real one
2952
1/1 [==============================] - 0s 20ms/step
For user:67671,  
the real recommendation: [2952]
[[0.3659055]]
Results:27216
the real one
1250
1/1 [==============================] - 0s 27ms/step
For user:82934,  
the real recommendation: [1250]
[[0.7424059]]
Results:27217
the real one
87234
1/1 [==============================] - 0s 21ms/step
For user:134067,  
the real recommendation: [87234]
[[0.04453681]]
Results:27217
the real one
32587
1/1 [==============================] - 0s 20ms/step
For user:41091,  
the real recommendation: [32587]
[[0.8419212]]
Results:27218
the real one
49286
1/1 [==============================] - 0s 20ms/step
For user:121606,  
the real recommendation: [49286]
[[0.31061476]]
Results:27218
the real one
292
1/1 [==============================] - 0s 21ms/step
For user:110476,  
the real recommendation: [292]
[[

For user:60286,  
the real recommendation: [30749]
[[0.73013747]]
Results:27256
the real one
3445
1/1 [==============================] - 0s 21ms/step
For user:895,  
the real recommendation: [3445]
[[0.07987701]]
Results:27256
the real one
61323
1/1 [==============================] - 0s 20ms/step
For user:119223,  
the real recommendation: [61323]
[[0.5877817]]
Results:27257
the real one
1248
1/1 [==============================] - 0s 23ms/step
For user:77470,  
the real recommendation: [1248]
[[0.5784395]]
Results:27258
the real one
2548
1/1 [==============================] - 0s 21ms/step
For user:103106,  
the real recommendation: [2548]
[[0.21746111]]
Results:27258
the real one
218
1/1 [==============================] - 0s 21ms/step
For user:59529,  
the real recommendation: [218]
[[0.5281708]]
Results:27259
the real one
3147
1/1 [==============================] - 0s 21ms/step
For user:120468,  
the real recommendation: [3147]
[[0.98772913]]
Results:27260
the real one
7371
1/1 [=====

the real one
1037
1/1 [==============================] - 0s 20ms/step
For user:107059,  
the real recommendation: [1037]
[[0.66316426]]
Results:27292
the real one
647
1/1 [==============================] - 0s 20ms/step
For user:120020,  
the real recommendation: [647]
[[0.72690123]]
Results:27293
the real one
994
1/1 [==============================] - 0s 20ms/step
For user:38604,  
the real recommendation: [994]
[[0.5731502]]
Results:27294
the real one
4280
1/1 [==============================] - 0s 20ms/step
For user:15586,  
the real recommendation: [4280]
[[0.34381974]]
Results:27294
the real one
65
1/1 [==============================] - 0s 20ms/step
For user:125766,  
the real recommendation: [65]
[[0.54673785]]
Results:27295
the real one
866
1/1 [==============================] - 0s 21ms/step
For user:25959,  
the real recommendation: [866]
[[0.66942036]]
Results:27296
the real one
905
1/1 [==============================] - 0s 20ms/step
For user:78388,  
the real recommendation: [9

1/1 [==============================] - 0s 21ms/step
For user:116159,  
the real recommendation: [597]
[[0.9991918]]
Results:27370
the real one
743
1/1 [==============================] - 0s 22ms/step
For user:32907,  
the real recommendation: [743]
[[0.6430531]]
Results:27371
the real one
420
1/1 [==============================] - 0s 20ms/step
For user:54839,  
the real recommendation: [420]
[[0.82026404]]
Results:27372
the real one
527
1/1 [==============================] - 0s 22ms/step
For user:43414,  
the real recommendation: [527]
[[0.99760854]]
Results:27373
the real one
47644
1/1 [==============================] - 0s 21ms/step
For user:79947,  
the real recommendation: [47644]
[[0.14645317]]
Results:27373
the real one
52722
1/1 [==============================] - 0s 21ms/step
For user:93625,  
the real recommendation: [52722]
[[0.5761404]]
Results:27374
the real one
47610
1/1 [==============================] - 0s 20ms/step
For user:118224,  
the real recommendation: [47610]
[[0.70

In [1]:
import numpy as np

In [9]:
a=np.array([[1],[2],[3]])
b=np.array([[6],[7],[8]])

In [12]:
c=np.concatenate((a,b))
        


In [13]:
c

array([[1],
       [2],
       [3],
       [6],
       [7],
       [8]])